# Stage three hyper parameters optimization #

## Parameters cell ##

Parameters are overiddent by papermill when run inside DVC stages



In [1]:
n_folds = 5 # this sets global setting of which how many bootstraps to use
n_hold_out = 1
repeats = 10
n_trials = 150
importance_type = "split"
n_ehvi_candidates = 12
trait = "lifespan"#"lifespan"
opt_metrics = "r2"
genes_num=10
stage_num=3
debug_local = True #to use local version

In [2]:
suffix=f"_{stage_num}"

In [3]:
from pathlib import Path
import sys
import inspect

local = (Path("..") / "yspecies").resolve()
if debug_local and local.exists():
  sys.path.insert(0, Path("..").as_posix())
  #sys.path.insert(0, local.as_posix())
  print("extending pathes with local yspecies")
  print(sys.path)
  %load_ext autoreload
  %autoreload 2

extending pathes with local yspecies
['..', '/data/sources/yspecies/notebooks', '/data/miniconda3/envs/yspecies/lib/python38.zip', '/data/miniconda3/envs/yspecies/lib/python3.8', '/data/miniconda3/envs/yspecies/lib/python3.8/lib-dynload', '', '/data/miniconda3/envs/yspecies/lib/python3.8/site-packages', '/data/miniconda3/envs/yspecies/lib/python3.8/site-packages/IPython/extensions', '/home/anton/.ipython']


In [4]:
from dataclasses import dataclass, replace
import numpy as np
import pandas as pd
from sklearn.pipeline import Pipeline
import seaborn as sns
import matplotlib.pyplot as plt

In [5]:
from typing import *
from yspecies.dataset import *
from yspecies.utils import *
from yspecies.workflow import TupleWith, Repeat, Collect
from yspecies.config import *
from yspecies.preprocess import FeatureSelection, DataExtractor
from yspecies.partition import DataPartitioner, PartitionParameters
from yspecies.tuning import Tune, MultiObjectiveResults
from yspecies.explanations import FeatureSummary, ShapSelector
from yspecies.selection import CrossValidator
import optuna
from optuna import Study, Trial

In [6]:
#settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)
import pprint
pp = pprint.PrettyPrinter(indent=4)

#charts settings
import matplotlib.pyplot as plt
from IPython.display import set_matplotlib_formats
%matplotlib auto
plt.ioff()
set_matplotlib_formats('svg')

Using matplotlib backend: agg


### Loading data ###
Let's load data from species/genes/expressions selected by select_samples.py notebook

In [7]:
from pathlib import Path
locations: Locations = Locations("./") if Path("./data").exists() else Locations("../")

In [8]:
from loguru import logger

logger.add(locations.logs / f"optimization_stage{suffix}_errors.log", backtrace=True, diagnose=True)
logger.add(locations.logs / f"optimization_stage{suffix}.log", rotation="12:00")     # New file is created each day at noon

2

In [9]:
data = ExpressionDataset.from_folder(locations.interim.stage(stage_num-1) / "input")
data

<table border='2'><caption>input<caption><tr><th>expressions</th><th>genes</th><th>species</th><th>samples</th><th>Genes Metadata</th><th>Species Metadata</th></tr><tr><td>(408, 154)</td><td>(154, 37)</td><td>38</td><td>408</td><td>(154, 2)</td><td>(38, 18)</td></tr></table>

### Loading genes from the ranked selection ###

In [10]:
intersections = locations.output.intersections
ranked = pd.read_csv(intersections / "intersections_ranked.tsv", sep="\t", index_col="reference_gene")
print(ranked.shape)
ranked.head(10)

(152, 23)


symbol   rank  ranks_sum  repeats_rank  shap_rank  \
reference_gene                                                         
ENSG00000188747     NOXA1  1.000     57.000         2.000     12.000   
ENSG00000170835       CEL  2.000     65.000         1.000      7.000   
ENSG00000136436  CALCOCO2  3.000     74.000         7.000     27.000   
ENSG00000198663   C6orf89  4.000     75.000        10.000     35.000   
ENSG00000172531    PPP1CA  5.000     80.000         5.000     42.000   
ENSG00000006282   SPATA20  6.000     86.000         8.000     25.000   
ENSG00000142002      DPP9  7.000     87.000         4.000     26.000   
ENSG00000129187      DCTD  8.000     89.000         8.000     32.000   
ENSG00000165501      LRR1  9.000     93.000         2.000     19.000   
ENSG00000120675   DNAJC15 10.000     94.000         8.000     52.000   

                 kendall_tau_rank  frequency_rank  tissue_linear_rank  \
reference_gene                                                          
ENSG00000188747            16.000           1.000              10.000   
ENSG00000170835             7.000           6.000              33.000   
ENSG00000136436             5.000           7.000              18.000   
ENSG00000198663             1.000           2.000              12.000   
ENSG00000172531             3.000          20.000              13.000   
ENSG00000006282            31.000          16.000               5.000   
ENSG00000142002            11.000          11.000              29.000   
ENSG00000129187            26.000           8.000               6.000   
ENSG00000165501            14.000           9.000              41.000   
ENSG00000120675             9.000          20.000               8.000   

                 genage_rank  repeats_all  repeats  mean_abs_shap  \
reference_gene                                                      
ENSG00000188747           17       19.000   10.000          0.507   
ENSG00000170835           17       20.000   10.000          0.849   
ENSG00000136436           17       14.000   10.000          0.307   
ENSG00000198663           17       10.000   10.000          0.226   
ENSG00000172531           17       16.000   10.000          0.165   
ENSG00000006282           17       13.000   10.000          0.311   
ENSG00000142002           17       17.000   10.000          0.309   
ENSG00000129187           17       13.000   10.000          0.253   
ENSG00000165501           17       19.000   10.000          0.366   
ENSG00000120675           17       13.000   10.000          0.128   

                 mean_kendall_tau  frequency  max_linear_r2  genage_count  \
reference_gene                                                              
ENSG00000188747             0.697      1.000          0.627         0.000   
ENSG00000170835             0.746      0.600          0.481         0.000   
ENSG00000136436             0.763      0.420          0.559         0.000   
ENSG00000198663            -0.788      0.940          0.616         0.000   
ENSG00000172531            -0.782      0.000          0.610         0.000   
ENSG00000006282             0.649      0.080          0.675         0.000   
ENSG00000142002            -0.717      0.300          0.507         0.000   
ENSG00000129187             0.674      0.400          0.666         0.000   
ENSG00000165501             0.715      0.340          0.459         0.000   
ENSG00000120675            -0.735      0.000          0.646         0.000   

                   direction  repeats_lifespan_stage_1  \
reference_gene                                           
ENSG00000188747   strong pro                     9.000   
ENSG00000170835   strong pro                    10.000   
ENSG00000136436   strong pro                     4.000   
ENSG00000198663  strong anti                     0.000   
ENSG00000172531  strong anti                     6.000   
ENSG00000006282   strong pro                     3.000   
ENSG00000142002  strong anti                     7.000   
E

In [11]:
def data_genes(genes: List[str]):
    return data.by_genes.collect(lambda gs: gs.loc[genes])

def data_head(num: int):
    return data_genes(ranked.head(num).index.to_list())

In [12]:
not_validated_species = data.min_max_trait(trait)
not_validated_species

['Mus_caroli', 'Homo_sapiens']

In [13]:
selection = FeatureSelection(
    samples = ["tissue","species"], #samples metadata to include
    species =  [], #species metadata other then Y label to include
    exclude_from_training = ["species"],  #exclude some fields from LightGBM training
    to_predict = trait, #column to predict
    categorical = ["tissue"],
    select_by = "shap",
    importance_type =  importance_type,
    feature_perturbation = "tree_path_dependent",
    not_validated_species = not_validated_species
)
selection

FeatureSelection(samples=['tissue', 'species'], species=[], genes=None, to_predict='lifespan', categorical=['tissue'], exclude_from_training=['species'], genes_meta=None, select_by='shap', importance_type='split', feature_perturbation='tree_path_dependent', not_validated_species=['Mus_caroli', 'Homo_sapiens'])

In [14]:
top_genes_data = data_head(genes_num)
top_genes_data

<table border='2'><caption>input<caption><tr><th>expressions</th><th>genes</th><th>species</th><th>samples</th><th>Genes Metadata</th><th>Species Metadata</th></tr><tr><td>(408, 10)</td><td>(10, 37)</td><td>38</td><td>408</td><td>(10, 2)</td><td>(38, 18)</td></tr></table>

## Setting up ShapSelector ##

Deciding on selection parameters (which fields to include, exclude, predict)

In [15]:
partition_params = PartitionParameters(n_folds, n_hold_out, 2,   42)

In [16]:
sampler_tpe = optuna.multi_objective.samplers.MOTPEMultiObjectiveSampler(
        n_ehvi_candidates=n_ehvi_candidates,
        seed=0
    )

MOTPEMultiObjectiveSampler is experimental (supported from v2.3.0). The interface can change in the future.
RandomMultiObjectiveSampler is experimental (supported from v1.4.0). The interface can change in the future.


In [17]:
def load_study(trait: str, suffix: str = suffix, sampler = sampler_tpe):
    url = f'sqlite:///' +str((locations.interim.optimization / (trait+suffix+".sqlite")).absolute())
    print('loading (if exists) study from '+url)
    storage = optuna.storages.RDBStorage(
        url=url
        #engine_kwargs={'check_same_thread': False}
    )
    return optuna.multi_objective.study.create_study(directions=['maximize','minimize','maximize'], 
                                                     storage = storage, 
                                                     study_name = f"{trait}_r2_huber_kendall", 
                                                     load_if_exists = True
                                                    )

study = load_study(trait, suffix)
study
#metrics, params = MultiObjectiveResults.from_study(study).best_metrics_params_r2()
#metrics, params

create_study is experimental (supported from v1.4.0). The interface can change in the future.
NSGAIIMultiObjectiveSampler is experimental (supported from v1.5.0). The interface can change in the future.
RandomMultiObjectiveSampler is experimental (supported from v1.4.0). The interface can change in the future.
[I 2020-11-15 03:28:33,166] Using an existing study with name 'lifespan_r2_huber_kendall' instead of creating a new one.


loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/lifespan_3.sqlite


MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.


In [18]:
def objective_parameters(trial: Trial) -> dict:
    return {
        'objective': 'regression',
        'metric': {'mae', 'mse', 'huber'},
        'verbosity': -1,
        'boosting_type': trial.suggest_categorical('boosting_type', ['dart', 'gbdt']),
        'lambda_l1': trial.suggest_uniform('lambda_l1', 0.01, 3.0),
        'lambda_l2': trial.suggest_uniform('lambda_l2', 0.01, 3.0),
        'max_leaves': trial.suggest_int("max_leaves", 15, 25),
        'max_depth': trial.suggest_int('max_depth', 3, 8),
        'feature_fraction': trial.suggest_uniform('feature_fraction', 0.4, 1.0),
        'bagging_fraction': trial.suggest_uniform('bagging_fraction', 0.3, 1.0),
        'learning_rate': trial.suggest_uniform('learning_rate', 0.01, 0.1),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 3, 8),
        'drop_rate': trial.suggest_uniform('drop_rate', 0.1, 0.3),
        "verbose": -1
    }
optimization_parameters = objective_parameters

In [19]:
from yspecies.workflow import SplitReduce

def side(i: int):
    print(i)
    return i

prepare_partition = SplitReduce(
    outputs = DataPartitioner(), 
    split = lambda x: [(x[0], replace(partition_params, seed=side(x[2])))], 
    reduce = lambda x, output: (output[0], x[1]) 
)                               
partition_and_cv = Pipeline(
    [
        ("prepare partition", prepare_partition),
        ("cross_validation", CrossValidator()),
        ("shap_computation", ShapSelector())
    ]
)

partition_and_cv_repeat =  Pipeline([
    ("repeat_cv_pipe", Repeat(partition_and_cv, repeats, lambda x, i: [x[0], x[1], i] )),
    ("collect_mean", Collect(fold=lambda results: (FeatureSummary(results).metrics_average.R2, FeatureSummary(results).metrics_average.huber, FeatureSummary(results).kendall_tau_abs_mean)))    
    ]
    )

p = Pipeline([
     ('extractor', DataExtractor()),
     ('tune', Tune(partition_and_cv_repeat, study = study, n_trials = n_trials, parameters_space = optimization_parameters))    
])

In [20]:
p = Pipeline([
     ('extractor', DataExtractor()),
     ('tune', Tune(partition_and_cv_repeat, study = study, n_trials = n_trials, parameters_space = optimization_parameters))    
])

In [21]:
results = p.fit_transform((top_genes_data, selection))
results

MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
MultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
2020-11-15 03:28:37.138 | INFO     | yspecies.selection:fit:157 - =

0
[LightGBM] [Warning] verbosity is set=-1, verbose=-1 will be ignored. Current value: verbosity=-1


Early stopping is not available in dart mode
2020-11-15 03:28:37.882 | INFO     | yspecies.selection:fit:161 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Heterocephalus_glaber', 'Capra_hircus']


[250]	valid_0's l1: 8.65398	valid_0's huber: 7.45687	valid_0's l2: 255.326


2020-11-15 03:28:38.530 | INFO     | yspecies.selection:fit:161 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Bos_taurus', 'Otolemur_garnettii']


...

[250]	valid_0's l1: 9.13046	valid_0's huber: 7.87252	valid_0's l2: 423.233


2020-11-15 05:14:35.184 | INFO     | yspecies.selection:fit:161 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Gorilla_gorilla', 'Microcebus_murinus']


[250]	valid_0's l1: 4.9989	valid_0's huber: 4.1818	valid_0's l2: 146.781
[250]	valid_0's l1: 6.81827	valid_0's huber: 5.7925	valid_0's l2: 114.211


2020-11-15 05:14:37.593 | INFO     | yspecies.explanations:transform:741 - Metrics: 
Metrics(R2=0.7098384068706246, MAE=7.293574991054809, MSE=225.07025281927872, huber=6.228124739417144)
MultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.
MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
[I 2020-11-15 05:14:37,993] Trial 323 finished with values: [0.7045401565481237, 5.9416328716433995, 0.6489309888810466] with parameters: {'boosting_type': 'dart', 'lambda_l1': 2.4730812060505447, 'lambda_l2': 0.2433075315611096, 'max_leaves': 16, 'max_depth': 5, 'feature_fraction': 0.5614787514499696, 'bagging_fraction': 0.6549913402207208, 'learning_rate': 0.07378821830446473, 'min_data_in_leaf': 5, 'drop_rate': 0.2592906278504832}.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.


MultiObjectiveResults(best_trials=[<optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7e3e20>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7e50a0>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7e5700>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7e5760>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7e5a60>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7cf5e0>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7b80a0>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7b81c0>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7be2e0>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7be400>, <optuna.multi_objective.trial.FrozenMultiObjectiveTrial object at 0x7fc25f7be760>, <optuna.multi_objective.trial.FrozenMultiObjectiveTr

In [23]:
results.best_trial_r2().values

(0.7177857732620769, 5.8991663803952825, 0.647131281750454)

In [ ]:
print("first optimization was finished")

In [ ]:
results.best_trial_r2().values

In [19]:
#optuna.multi_objective.visualization.plot_pareto_front(study, include_dominated_trials =True)